In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
plt.style.use('paper_1column.mplstyle')
import datetime
import time
import os
import sys
from pathlib import Path
import folium
import branca.colormap as cm
from folium.plugins import HeatMap

In [2]:
from sklearn.preprocessing import PolynomialFeatures
from sklearn import linear_model

In [3]:
def fit_trans(X):
    poly = PolynomialFeatures(degree = deg)
    X_ = poly.fit_transform(X) 
    #print(poly.get_feature_names_out(input_features=["TimeSec", "Lat", "Long"]))
    return X_

In [4]:
def standardize(V):
    if np.std(V) == 0:
        return np.zeros((len(V),1))
    else: 
        return((V-np.mean(V))/np.std(V))

In [5]:
def convert24(tim):
    # Parse the time string into a datetime object
    t = datetime.datetime.strptime(tim, '%I:%M:%S %p')
    # Format the datetime object into a 24-hour time string
    return t.strftime('%H:%M:%S')

In [6]:
def gen_darkhours(X1, y1):
    X2 = np.zeros((1,3))
    y2 = np.zeros((1,1))
    X1_ = np.copy(X1)
    y1_ = np.zeros((len(X1),1))
    y1_[:] = np.random.normal(8.83, 0.2, size=(len(X1),1))
    for i in [22, 23, 0, 1, 2, 3, 4, 5, 6]:
        X1_[:,2] = i*3600
        X2 = np.concatenate((X2,X1_))
        y2 = np.concatenate((y2,y1_))
    y1_[:] = np.random.normal(7.5, 0.2, size=(len(X1),1))
    for i in [21, 7]:
        X1_[:,2] = i*3600
        X2 = np.concatenate((X2,X1_))
        y2 = np.concatenate((y2,y1_))
    X2 = X2[1:,:]
    y2 = y2[1:,:]
    return X2, y2

In [7]:
def data_process(filename):
    data_pd = pd.read_csv(filename, sep=',',header=0, usecols = range(6))
    data_pd.columns = ['StartTime','Lat','Long','Velocity','Time','Time Offset']
    data_pd = data_pd.dropna()
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
    data_pd = data_pd.drop(range(num_rows-10, num_rows))
    data_pd = data_pd.drop(range(10))
    data_pd = data_pd.reset_index(drop=True)
    drop_arr = []
    num_rows = len(data_pd["Lat"])
    for i in range(num_rows):
        if "Err" in data_pd.iloc[i]['StartTime']:
            drop_arr.append(i)
    data_pd = data_pd.drop(drop_arr)
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
    drop_arr2 = []
    for i in range(num_rows):
        if "NUM" in data_pd.iloc[i]['StartTime']:
            drop_arr2.append(i)
    data_pd = data_pd.drop(drop_arr2)
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
#     for i in range(num_rows-1):
#         vel_vec[i] = np.sqrt((data_pd.iloc[i+1]["Lat"] - data_pd.iloc[i]["Lat"])**2\
#                              + (data_pd.iloc[i+1]["Long"] - data_pd.iloc[i]["Long"])**2)
#                              #+ (data_pd.iloc[i+1]["Altitude"] - data_pd.iloc[i]["Altitude"])**2)\
#         #/(data_pd.iloc[i+1]["TimeNano"]/10**9 - data_pd.iloc[i]["TimeNano"]/10**9)
    lat_vec = np.array(data_pd["Lat"])
    long_vec = np.array(data_pd["Long"])
#     conj_vec = 1/np.exp(vel_vec)
    time_vec = np.array(data_pd["StartTime"])
    vel_vec = np.array(data_pd["Velocity"])
    time_sec_vec = []
    for i in range(num_rows):
        if 'AM' not in time_vec[i] and 'PM' not in time_vec[i]:
            x = time.strptime(time_vec[i],'%H:%M:%S')
            time_sec_vec.append(datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds())
        else:
#             print(time_vec[i])
#             print(convert24(time_vec[i]))
            x = time.strptime(convert24(time_vec[i]),'%H:%M:%S')
            time_sec_vec.append(datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds())
            
    #X = np.transpose(np.array([lat_vec, long_vec, time_sec_vec]))
    X = np.transpose(np.array([lat_vec.astype(float), long_vec.astype(float), time_sec_vec]))
    y = np.zeros((num_rows, 1))
    for i in range(num_rows):
        y[i] = vel_vec[i]
    i = 0
    while i < len(X):
        if float(X[i,0]) < 37.42+0.0026:
            X = np.delete(X, (i), axis = 0)
            y = np.delete(y, (i), axis = 0)
            i = i - 1
        if float(X[i,0]) < 37.42+0.0043 and float(X[i,1]) > -122.1-0.0605:
            X = np.delete(X, (i), axis = 0)
            y = np.delete(y, (i), axis = 0)
            i = i - 1
        i = i + 1
    return X, y

In [8]:
Dark = True
Time_dep = False

Directory = '/Users/shirleychen/Documents/Winter2023/AA272/Project/GoodCSVs/'
pathlist = Path(Directory).rglob('*.csv')
X_real = np.zeros((1,3))
y_real = np.zeros((1,1))
X_dark = np.zeros((1,3))
y_dark = np.zeros((1,1))
for path in pathlist:
    X1, y1 = data_process(path)
    X2, y2 = gen_darkhours(X1, y1)
    X_dark = np.concatenate((X_dark,X2))
    y_dark = np.concatenate((y_dark,y2))
    X_real = np.concatenate((X_real,X1))
    y_real = np.concatenate((y_real,y1))
X_real = X_real[1:,:]
y_real = y_real[1:,:]
X_dark = X_dark[1:,:]
y_dark = y_dark[1:,:]
if Dark == True:
    X = np.concatenate((X_real,X_dark))
    y = np.concatenate((y_real,y_dark))
else:
    X = np.copy(X_real)
    y = np.copy(y_real)
print("Real data size:", np.size(y_real))
print("Dark data size:", np.size(y_dark))
print("Total data size:", np.size(y))

if Time_dep == False:
    X = X[:,0:2]
    X_real = X_real[:,0:2]
    X_dark = X_dark[:,0:2]

Real data size: 6875
Dark data size: 75625
Total data size: 82500


In [9]:
deg = 1
X_trans_first = fit_trans(X)
clf_first = linear_model.LinearRegression()
model_first = clf_first.fit(X_trans_first, y)
print("Degree 1 fit coefficients", model_first.coef_[0,1:4])

deg = 2
X_trans = fit_trans(X)
clf = linear_model.LinearRegression()
model = clf.fit(X_trans, y)

Degree 1 fit coefficients [11.61271666 14.47896891]


In [10]:
num_rows = len(X_real)
latlon_full = []
for i in range(num_rows):
    latlon_full.append((X_real[i,0], X_real[i,1]))
linear_y = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(y_real,0.05), vmax=np.quantile(y_real,0.95))

In [11]:
map_raw = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon_full):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_y(y_real[i]), radius=3,\
                  color=linear_y(y_real[i]), fill_opacity=0.5, opacity = 0.5).add_to(map_raw)
map_raw

In [12]:
linear_y

In [13]:
Directory = '/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/'
pathlist = Path(Directory).rglob('*.csv')
X_pred = np.zeros((1,3))
y_pred = np.zeros((1,1))
for path in pathlist:
    X1, y1 = data_process(path)
    X_pred = np.concatenate((X_pred,X1))
    y_pred = np.concatenate((y_pred,y1))
X_pred = X_pred[1:,:]
y_pred = y_pred[1:,:]

if Time_dep == False:
    X = X[:,0:2]
    X_pred = X_pred[:,0:2]

In [40]:
single_time = False
time_choice = "00:00:00"

Xp = np.copy(X_pred)
if single_time == True:
    x = time.strptime(time_choice,'%H:%M:%S')
    time_sec = datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds()
    print("Time in seconds:", time_sec)
    if Time_dep == True:
        Xp[:,2] = time_sec
Xp_ = fit_trans(Xp)
yp = clf.predict(Xp_)

In [41]:
num_rows = len(X_pred)
latlon = []
for i in range(num_rows):
    latlon.append((X_pred[i,0], X_pred[i,1]))
linear_yp = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(yp,0.05), vmax=np.quantile(yp,0.95))

map_pred_scale = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_yp(yp[i]), radius=3,\
                  color=linear_yp(yp[i]), fill_opacity=0.5,).add_to(map_pred_scale)
map_pred_scale

In [16]:
linear_yp

In [17]:
# for if standardizing
map_raw_scale = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_y(yp[i]), radius=3,\
                  color=linear_y(yp[i]), fill_opacity=1.0,).add_to(map_raw_scale)
map_raw_scale

In [18]:
print("Max Lat:", np.max(X_real[:,0]))
print("Min Lat:", np.min(X_real[:,0]))
print("Max Long:", np.max(X_real[:,1]))
print("Min Long:", np.min(X_real[:,1]))

Max Lat: 37.42941173
Min Lat: 37.4226004
Max Long: -122.1594655
Min Long: -122.1731369


In [34]:
Lat_vec = np.linspace(np.min(X_real[:,0]), np.max(X_real[:,0]), 20)
Long_vec = np.linspace(np.min(X_real[:,1]), np.max(X_real[:,1]), 30)
Coord_mat = []
for i in range(len(Lat_vec)):
    for j in range(len(Long_vec)):
        Coord_mat.append([Lat_vec[i], Long_vec[j]])
Xp_mat = np.copy(Coord_mat)
Xp_mat_ = fit_trans(Xp_mat)
#yp_mat = clf.predict(Xp_mat_)
yp_mat = np.ones((len(Xp_mat), 1))*0
Coord_mat = np.concatenate((Coord_mat, yp_mat),axis = 1)
Heat_mat = np.concatenate((Coord_mat,np.concatenate((latlon_full, y_real),axis = 1)))
print(Heat_mat[:,2])

[0.       0.       0.       ... 8.856831 8.9      8.899431]


In [37]:
map_heat = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
HeatMap(Heat_mat, min_opacity=0.4, radius=11, blur=15,\
        gradient={0.4: 'green', 0.65: 'yellow', 1: 'red'}).add_to(map_heat)
map_heat